In [ ]:
df = sqlContext.read.format("com.databricks.spark.csv").option("header", "true").option("inferschema", "true").load("/data/MSA_8050_Spring_18/proj09/final_merged_data.csv")

In [8]:
df.printSchema()

root
 |-- bus_business_id: string (nullable = true)
 |-- business_name: string (nullable = true)
 |-- neighborhood: string (nullable = true)
 |-- address: string (nullable = true)
 |-- city: string (nullable = true)
 |-- state: string (nullable = true)
 |-- postal_code: string (nullable = true)
 |-- latitude: double (nullable = true)
 |-- longitude: double (nullable = true)
 |-- stars: double (nullable = true)
 |-- review_count1: integer (nullable = true)
 |-- is_open: integer (nullable = true)
 |-- categories: string (nullable = true)
 |-- review_id: string (nullable = true)
 |-- user_id: string (nullable = true)
 |-- business_id: string (nullable = true)
 |-- review_stars: integer (nullable = true)
 |-- review_date: string (nullable = true)
 |-- text: string (nullable = true)
 |-- review_useful: integer (nullable = true)
 |-- review_funny: integer (nullable = true)
 |-- review_cool: integer (nullable = true)
 |-- user_user_id: string (nullable = true)
 |-- user_name: string (nullable

In [9]:
li=['business_name', 'bus_business_id',
 'neighborhood', 'city' , 'state',
 'address','postal_code',
 'latitude', 'stars','review_id',
 'longitude','is_open', 'review_count1',
 'categories','review_date','yelping_since',
 'friends','review_stars','review_useful','review_funny',
 'user_useful','review_cool','user_id'
 'user_funny','user_name','review_count',
 'user_cool','business_id','user_id','user_funny',
 'user_user_id','average_stars',
 'elite', 'compliment_hot',
 'compliment_more',
 'compliment_profile',
 'compliment_cute',
 'compliment_list',
 'compliment_note',
 'compliment_plain',
 'compliment_cool',
 'compliment_funny',
 'compliment_writer',
 'compliment_photos']

In [10]:
for i in li:
    df=df.drop(i)

In [11]:
df.count()

5251828

In [4]:
df.printSchema()

root
 |-- text: string (nullable = true)
 |-- fans: integer (nullable = true)



In [6]:
df.select('fans').show()

+----+
|fans|
+----+
|   0|
|   1|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
|   0|
+----+
only showing top 20 rows



In [12]:
df1 = df.where(df["fans"]>0)

In [42]:
df1.printSchema()

root
 |-- text: string (nullable = true)
 |-- fans: integer (nullable = true)



In [13]:
df2 = df1.sort("fans", ascending=False)

In [ ]:
df2.count()

2566452

In [ ]:
 # the number selected
df2.where(df1['fans'] !=0).count()

In [42]:
# num = 10%* the number selected
df3 = df2.select('text').take(256645) 

In [45]:
df3

[Row(text=u"Wish the food selection was broader... bagels, danishes, and not much else. I bought a muffin I'm pretty sure was made by Otis Spunkmeyer (since they have an oven with the brand's name on it). It was dry, despite being ordered in the a.m. Didn't like it, but I liked everything else about this place! Really nice gal who served up a good latte -- and quickly."),
 Row(text=u"Marriotts generally seem to be awesome on the surface, but lose their luster the closer you look (no free internet. no in-room coffee maker?!). I still had a good experience, though, in the short time I stayed here. Plenty of parking, and a friendly front-desk, made for a nice welcome after an annoying drive. My room was clean, very spacious, and I love the varying-density pillows on the bed. Bath & Body Works in the bathroom. Restaurant is open til midnight, which is convenient; though I didn't have a chance to check it out. Elevator was reasonably quick. And the decor -- heavy curtains, red and gilt acce

In [ ]:
#Upload the csv file as RDD

In [47]:
with open("10%fanstext.txt", "w") as output:
    output.write(str(df3))  

In [48]:
%%bash

hdfs dfs -copyFromLocal /home/ccheang1/proj09/fanstext.txt /data/MSA_8050_Spring_18/proj09

In [ ]:
#Getting top words

In [ ]:
from pyspark import SparkConf, SparkContext
from pyspark import sql
from pyspark.sql import SQLContext
from pyspark.sql.functions import avg

# conf=SparkConf().setMaster('yarn-client').setAppName("t1")

conf=SparkConf().setAppName("t1") #####local
sc=SparkContext(conf=conf) 
sqlContext = sql.SQLContext(sc)

In [49]:
lines = sc.textFile("/data/MSA_8050_Spring_18/proj09/fanstext.txt")

In [50]:
import string

import operator  
import nltk
import numpy as np 
from nltk.corpus import stopwords

nltk.download('stopwords') 

[u'[Row(text=u"Wish the food selection was broader... bagels, danishes, and not much else. I bought a muffin I\'m pretty sure was made by Otis Spunkmeyer (since they have an oven with the brand\'s name on it). It was dry, despite being ordered in the a.m. Didn\'t like it, but I liked everything else about this place! Really nice gal who served up a good latte -- and quickly."), Row(text=u"Marriotts generally seem to be awesome on the surface, but lose their luster the closer you look (no free internet. no in-room coffee maker?!). I still had a good experience, though, in the short time I stayed here. Plenty of parking, and a friendly front-desk, made for a nice welcome after an annoying drive. My room was clean, very spacious, and I love the varying-density pillows on the bed. Bath & Body Works in the bathroom. Restaurant is open til midnight, which is convenient; though I didn\'t have a chance to check it out. Elevator was reasonably quick. And the decor -- heavy curtains, red and gil

In [51]:
#Remove all the puctuation in the text and convert to lower case 
rdd1=lines.map(lambda x: (''.join([i for i in x if i not in string.punctuation] ))).map(lambda x: x.lower()) 
#Remove all the stop words and numbers 
stop = list(stopwords.words('english')) 
add_list = ['','1','2','3','4','5','6','7','8','9','0']
stop.extend(add_list)

[u'rowtextuwish the food selection was broader bagels danishes and not much else i bought a muffin im pretty sure was made by otis spunkmeyer since they have an oven with the brands name on it it was dry despite being ordered in the am didnt like it but i liked everything else about this place really nice gal who served up a good latte  and quickly rowtextumarriotts generally seem to be awesome on the surface but lose their luster the closer you look no free internet no inroom coffee maker i still had a good experience though in the short time i stayed here plenty of parking and a friendly frontdesk made for a nice welcome after an annoying drive my room was clean very spacious and i love the varyingdensity pillows on the bed bath  body works in the bathroom restaurant is open til midnight which is convenient though i didnt have a chance to check it out elevator was reasonably quick and the decor  heavy curtains red and gilt accents  feels ritzy very convenient to southpark and you cou

In [52]:
rdd2 = rdd1.map(lambda x: [i for i in x.split(' ') if i not in stop])
#rdd2 is a list of words in a list; take it from one list 
rdd3= rdd2.flatMap(lambda x:x)
ls = rdd3.collect()

[u'i',
 u'me',
 u'my',
 u'myself',
 u'we',
 u'our',
 u'ours',
 u'ourselves',
 u'you',
 u"you're",
 u"you've",
 u"you'll",
 u"you'd",
 u'your',
 u'yours',
 u'yourself',
 u'yourselves',
 u'he',
 u'him',
 u'his',
 u'himself',
 u'she',
 u"she's",
 u'her',
 u'hers',
 u'herself',
 u'it',
 u"it's",
 u'its',
 u'itself',
 u'they',
 u'them',
 u'their',
 u'theirs',
 u'themselves',
 u'what',
 u'which',
 u'who',
 u'whom',
 u'this',
 u'that',
 u"that'll",
 u'these',
 u'those',
 u'am',
 u'is',
 u'are',
 u'was',
 u'were',
 u'be',
 u'been',
 u'being',
 u'have',
 u'has',
 u'had',
 u'having',
 u'do',
 u'does',
 u'did',
 u'doing',
 u'a',
 u'an',
 u'the',
 u'and',
 u'but',
 u'if',
 u'or',
 u'because',
 u'as',
 u'until',
 u'while',
 u'of',
 u'at',
 u'by',
 u'for',
 u'with',
 u'about',
 u'against',
 u'between',
 u'into',
 u'through',
 u'during',
 u'before',
 u'after',
 u'above',
 u'below',
 u'to',
 u'from',
 u'up',
 u'down',
 u'in',
 u'out',
 u'on',
 u'off',
 u'over',
 u'under',
 u'again',
 u'further',
 u'th

In [ ]:
#Remove stemming words
from nltk.stem import *
stemmer=PorterStemmer() 
singles=[stemmer.stem(word) for word in ls ] 

In [ ]:
#Save stingles to text file  
rdd_single = sc.parallelize(singles)

In [ ]:
#Get word frequency 
from operator import add 

rdd4=rdd_single.map(lambda word: (word,1)).reduceByKey(add).sortBy(lambda x: x[1],ascending = False)

In [ ]:
#Convert rdd4 to DF  
df_rev_use= rdd4.toDF(['word','count'])

df_rev_use.repartition(1).write.format("com.databricks.spark.csv").option("header", "true").save("fans_word.csv")